In [1]:
import pandas as pd
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt
import plotly.express as px
import plotly.graph_objects as go

In [2]:
path = "C:/Users/82104/Downloads/Insurance_fraud/"
df = pd.read_csv(path + "fraud_oracle.csv")
df.head()

Month  WeekOfMonth  DayOfWeek    Make AccidentArea DayOfWeekClaimed  \
0   Dec            5  Wednesday   Honda        Urban          Tuesday   
1   Jan            3  Wednesday   Honda        Urban           Monday   
2   Oct            5     Friday   Honda        Urban         Thursday   
3   Jun            2   Saturday  Toyota        Rural           Friday   
4   Jan            5     Monday   Honda        Urban          Tuesday   

  MonthClaimed  WeekOfMonthClaimed     Sex MaritalStatus  ...  AgeOfVehicle  \
0          Jan                   1  Female        Single  ...       3 years   
1          Jan                   4    Male        Single  ...       6 years   
2          Nov                   2    Male       Married  ...       7 years   
3          Jul                   1    Male       Married  ...   more than 7   
4          Feb                   2  Female        Single  ...       5 years   

  AgeOfPolicyHolder PoliceReportFiled WitnessPresent AgentType  \
0          26 to 30                No             No  External   
1          31 to 35               Yes             No  External   
2          41 to 50                No             No  External   
3          51 to 65               Yes             No  External   
4          31 to 35                No             No  External   

   NumberOfSuppliments  AddressChange_Claim  NumberOfCars  Year  BasePolicy  
0                 none               1 year        3 to 4  1994   Liability  
1                 none            no change     1 vehicle  1994   Collision  
2                 none            no change     1 vehicle  1994   Collision  
3          more than 5            no change     1 vehicle  1994   Liability  
4                 none            no change     1 vehicle  1994   Collision  

[5 rows x 33 columns]

# 각 컬럼 이해하기
비슷한 컬럼끼리 정리한다. 나중에 인사이트 뽑을 때 유용하다.
## 사고날짜
- Month : 월 - 사고가 발생한 월
- WeekOfMonth : 월의 주 - 사고가 발생한 주
- DayOfWeek : 요일 - 사고가 발생한 요일

## 사고 접수 날짜
- DayOfWeekClaimed : 클레임 요일 - 보험 청구가 접수된 요일
- MonthClaimed : 클레임 월 - 보험 청구가 접수된 월
- WeekOfMonthClaimed : 클레임 주 - 보험 청구가 접수된 주
- Year : 연도 - 사고가 발생한 연도

## 차량 정보
- Make : 제조사 - 차량의 제조사
- VehicleCategory : 차량 분류 - 차량의 분류(예: 승용차, 트럭 등)
- VehiclePrice : 차량 가격 - 차량의 가격 범위
- AgeOfVehicle : 차량 연식 - 차량의 연식

## 사고 정보
- AccidentArea : 사고 지역 - 사고가 발생한 지역(도시/농촌)
- Fault : 책임 - 사고에 대한 책임 여부(보험 가입자/타인)
- RepNumber : 보고서 번호 - 사고 보고서의 고유 번호
- PoliceReportFiled : 경찰 보고서 제출 여부 - 사고 후 경찰 보고서 제출 여부
- WitnessPresent : 목격자 존재 여부 - 사고 당시 목격자 존재 여부
- NumberOfSuppliments : 추가 수리 항목 - 차량 수리를 위해 필요한 추가 수리 항목

## 가입자 정보
- Sex : 성별 - 보험 가입자의 성별
- MaritalStatus : 결혼 여부 - 보험 가입자의 결혼상태
- Age : 나이 - 보험 가입자의 나이
- AgeOfPolicyHolder : 보험 가입자 나이 - 보험 가입자의 나이
- PastNumberOfClaims : 과거 청구 건수 - 이전에 청구한 보험 건수
- DriverRating : 운전자 등급 - 운전자의 평가 등급

## 보험 상품 정보
- PolicyNumber : 정책 번호 - 보험 정책의 고유 번호
- PolicyType : 정책 유형 - 보험 정책의 유형
- Deductible : 공제액 - 보험 청구 시 가입자가 부담해야 하는 금액
- BasePolicy : 기본 정책 - 기본 보험 정책 유형
- AgentType : 에이전트 유형 - 보험 에이전트의 유형
- NumberOfCars : 차량 수 - 보험 정채에 포함된 차량 수

## 보험 사기 여부
- FraudFound_P : 사기 발견 여부 - 보험 청구가 사기인지를 나타냄 (0: 정상, 1: 사기)

In [25]:
print(df.FraudFound_P.unique(),'\n\n',df.PolicyType.unique())

[0 1] 

 ['Sport - Liability' 'Sport - Collision' 'Sedan - Liability'
 'Utility - All Perils' 'Sedan - All Perils' 'Sedan - Collision'
 'Utility - Collision' 'Utility - Liability' 'Sport - All Perils']


In [26]:
print(df.FraudFound_P.value_counts(),'\n\n' ,df.PolicyType.value_counts())

FraudFound_P
0    14497
1      923
Name: count, dtype: int64 

 PolicyType
Sedan - Collision       5584
Sedan - Liability       4987
Sedan - All Perils      4087
Sport - Collision        348
Utility - All Perils     340
Utility - Collision       30
Sport - All Perils        22
Utility - Liability       21
Sport - Liability          1
Name: count, dtype: int64


df 전반적으로 확인

df.shape # 로우, 칼럼 갯수 확인
df.nunique() # 각 칼럼의 고유값 갯수
df.info() # 칼럼들 정보, null, Dtype
df.describe() # df의 기초통계들

df.isnull().sum() # null 갯수 / False : 0, True : 1

가끔 Numerical 데이터의 null을 999 혹은 0 으로 넣고,
Categorical 데이터면 "Null" 이라는 str값을 넣을 때도 있으니 조심해야함

### 시각화
- count plot
- histogram

In [27]:
# 결혼여부에 따른 범죄 유무
px.histogram(df, x="MaritalStatus", title="Count plot of MaritalStatus", color="FraudFound_P")

In [28]:
# Pandas Series는 컬럼이랑 다르게 왼쪽이 index 오른쪽이 value
df['MaritalStatus'].value_counts().index

Index(['Married', 'Single', 'Divorced', 'Widow'], dtype='object', name='MaritalStatus')

In [29]:
px.histogram(df, x="MaritalStatus", title = "Count plot of MaritalStatus",
             category_orders = df['MaritalStatus'].value_counts().index)

# category_orders=['Married', 'Single', 'Divorced', 'Widow']

In [30]:
# dir(px) : px. 해서 활용할수 있는 것을 확인할 수 있다.
# 그래도 모르면 help(px.histogram)

# Numerical data graph
px.histogram(df, x = 'Age', title = "Histogram of Age")
# 아래에 0살이 320 카운트됨. 즉 0으로 Null을 처리함

In [57]:
# 이미 한번 임포트 된 모듈은 다시 임포트 구문을 실행시킨다 해도 변경된 내용이 인터프리터 상에 적용

# Load tools
import importlib
import utils

importlib.reload(utils) # 코드를 수정했을 때, 커널을 재시작하지 않고도 변경된 내용을 반영할 수 있습니다.
from utils import histogram_plot # 수정된 함수를 특정지어 한번 더 해줘야함.
from utils import count_plot
from utils import make_graph

In [60]:
make_graph(df)